In [ ]:
import json
import numpy as np

data = json.load(open("scene/gaussians_3dgs.json"))
colors = np.array(data["colors"])
print("Color shape:", colors.shape)
print("Mean color:", colors.mean(axis=0))
print("Min color:", colors.min(axis=0))
print("Max color:", colors.max(axis=0))
print("Color range:", colors.max(axis=0) - colors.min(axis=0))
print("Color stddev:", colors.std(axis=0))

In [1]:
import open3d as o3d
pcd = o3d.io.read_point_cloud("scene/pointcloud.ply")
o3d.visualization.draw_geometries([pcd])


Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
[Open3D WARNING] GLFW Error: Failed to detect any supported platform
[Open3D WARNING] GLFW initialized for headless rendering.
[Open3D WARNING] GLFW Error: OSMesa: Library not found
[Open3D WARNING] Failed to create window
[Open3D WARNING] [DrawGeometries] Failed creating OpenGL window.


In [2]:
import json
data = json.load(open("scene/gaussians_3dgs_fixed.json"))
print("Keys:", data.keys())
print("Example SH:", data["shs"][0][:3])
print("Example Scale:", data["scales"][0])
print("Example Rotation:", data["rotations"][0])


Keys: dict_keys(['positions', 'scales', 'rotations', 'shs'])
Example SH: [0.35435381531715393, 0.28175750374794006, 0.2843777537345886]
Example Scale: [14.785829672222592, 14.754964111218042, 0.0114359242955411]
Example Rotation: [9.82606518997748e-17, 5.7881314077609935e-18, 9.88139834763871e-18, 0.9999999999999998]


In [3]:
import json
import numpy as np

with open("scene/gaussians_3dgs_fixed.json") as f:
    d = json.load(f)

sh = np.array([x[:3] for x in d["shs"]])  # only RGB
print("Mean RGB:", np.mean(sh, axis=0))
print("Max RGB:", np.max(sh, axis=0))
print("Min RGB:", np.min(sh, axis=0))


Mean RGB: [0.38426859 0.33975994 0.37163101]
Max RGB: [0.40153188 0.3764706  0.43290442]
Min RGB: [0.34390619 0.27485391 0.27906382]


In [4]:
from plyfile import PlyData
plydata = PlyData.read("scene/pointcloud.ply")
points = np.array([list(v) for v in plydata['vertex'].data])
print("Bounding box:")
print("  Min:", points.min(axis=0))
print("  Max:", points.max(axis=0))
print("  Size:", points.max(axis=0) - points.min(axis=0))


Bounding box:
  Min: [-198.60973 -101.52769 -180.36012    5.         0.         0.     ]
  Max: [205.29234 115.81007 201.72792 255.      255.      255.     ]
  Size: [403.90207 217.33775 382.08804 250.      255.      255.     ]


In [6]:
from PIL import Image
img = Image.open("scene_init/images/000.png")
print("Pixel stats:", np.array(img).mean(axis=(0,1)))


Pixel stats: [178. 178. 178.]


In [7]:
from plyfile import PlyData
import numpy as np

ply = PlyData.read("scene/pointcloud.ply")
data = ply['vertex'].data
rgb = np.stack([data['red'], data['green'], data['blue']], axis=1) / 255.0

print("RGB stats: mean =", np.mean(rgb, axis=0), "min =", np.min(rgb, axis=0), "max =", np.max(rgb, axis=0))


RGB stats: mean = [0.33193548 0.27852608 0.27626476] min = [0.01960784 0.         0.        ] max = [1. 1. 1.]


In [8]:
from plyfile import PlyData
import numpy as np

ply = PlyData.read("scene/pointcloud.ply")
data = ply['vertex'].data

rgb = np.stack([data['red'], data['green'], data['blue']], axis=1) / 255.0
print("RGB mean:", np.mean(rgb, axis=0))
print("RGB min:", np.min(rgb, axis=0))
print("RGB max:", np.max(rgb, axis=0))



RGB mean: [0.33193548 0.27852608 0.27626476]
RGB min: [0.01960784 0.         0.        ]
RGB max: [1. 1. 1.]


In [2]:
from plyfile import PlyData
import numpy as np
import plotly.graph_objects as go
import json

# Adjust paths:
PLY_PATH = 'scene/pointcloud.ply'
TRANSFORMS = 'scene_init/transforms_train.json'

# Load with plyfile
ply = PlyData.read(PLY_PATH)
v = ply['vertex'].data
xyz = np.vstack([v['x'], v['y'], v['z']]).T
rgb = np.vstack([v['red'], v['green'], v['blue']]).T / 255.0

# Subsample
idx = np.random.choice(len(xyz), min(100000, len(xyz)), replace=False)
xyz, rgb = xyz[idx], rgb[idx]

# Load camera
frames = json.load(open(TRANSFORMS))['frames']
cam = np.array(frames[0]['transform_matrix'])
cam_pos = cam[:3,3]

# Frustum (same as before)...
fov, aspect, near = np.deg2rad(60), 512/256, 1.0
h, w = np.tan(fov/2)*near, np.tan(fov/2)*near*aspect
corners = np.array([[ w,h,near],[-w,h,near],[-w,-h,near],[w,-h,near],[0,0,0]])
world = (cam[:3,:3] @ corners.T).T + cam_pos

# Plot
pc = go.Scatter3d(x=xyz[:,0], y=xyz[:,1], z=xyz[:,2],
                  mode='markers', marker=dict(size=1, color=rgb))
lines = [go.Scatter3d(x=[cam_pos[0], world[i,0]],
                      y=[cam_pos[1], world[i,1]],
                      z=[cam_pos[2], world[i,2]],
                      mode='lines', line=dict(color='red', width=2))
         for i in range(4)]
fig = go.Figure(data=[pc]+lines)
fig.update_layout(scene=dict(aspectmode='data'),
                  title="Point Cloud + Camera Frustum")
fig.show()


In [7]:
import numpy as np
import json
from plyfile import PlyData
from PIL import Image
import os

PLY_PATH        = "scene/pointcloud.ply"
TRANSFORMS_JSON = "scene_init/transforms_train.json"
OUT_DIR         = "scene_init_offscreen_fixed"
IMG_W, IMG_H    = 512, 256
FX = FY = 0.5 * IMG_W
CX, CY = 0.5 * IMG_W, 0.5 * IMG_H

os.makedirs(OUT_DIR, exist_ok=True)

# Load once
ply = PlyData.read(PLY_PATH)
v   = ply['vertex'].data
xyz = np.vstack([v['x'], v['y'], v['z']]).T.astype(np.float32)
rgb = np.vstack([v['red'], v['green'], v['blue']]).T.astype(np.float32)/255.0

frames = json.load(open(TRANSFORMS_JSON))['frames']

# Compute coverages (as before)...
coverages = []
for idx, frm in enumerate(frames):
    M = np.array(frm['transform_matrix'], dtype=np.float32)
    R,t = M[:3,:3], M[:3,3]
    Xc = (xyz - t) @ R.T
    zs = Xc[:,2]
    mask = zs>0
    Xc, zs = Xc[mask], zs[mask]
    us = np.round((FX*Xc[:,0]/zs)+CX).astype(int)
    vs = np.round((FY*Xc[:,1]/zs)+CY).astype(int)
    valid = (us>=0)&(us<IMG_W)&(vs>=0)&(vs<IMG_H)
    coverages.append((idx, valid.sum()))
coverages.sort(key=lambda x: x[1], reverse=True)
top_views = [idx for idx,_ in coverages[:5]]
print("Top-5 views:", top_views)

# Rasterize & save, with warning suppression
for idx in top_views:
    frm = frames[idx]
    M_c2w = np.array(frm['transform_matrix'], dtype=np.float32)
    M_w2c = np.linalg.inv(M_c2w)
    R = M_w2c[:3,:3]
    t = M_w2c[:3,3]
    
    Xc = (xyz @ R.T) + t
    zs = Xc[:,2]
    mask = zs > 0
    Xc, zs, cols = Xc[mask], zs[mask], rgb[mask]
    us = np.round((FX*Xc[:,0]/zs)+CX).astype(int)
    vs = np.round((FY*Xc[:,1]/zs)+CY).astype(int)
    valid = (us>=0)&(us<IMG_W)&(vs>=0)&(vs<IMG_H)
    us, vs, zs, cols = us[valid], vs[valid], zs[valid], cols[valid]

    img = np.zeros((IMG_H,IMG_W,3), dtype=np.uint8)
    depth = np.full((IMG_H,IMG_W), np.inf, dtype=np.float32)
    for u,v,z,c in zip(us,vs,zs,cols):
        if z < depth[v,u]:
            depth[v,u] = z
            img[v,u]   = (c*255).astype(np.uint8)

    # Now normalize depth safely
    valid_d = np.isfinite(depth)
    depth_vis = np.zeros_like(depth, dtype=np.uint8)
    if valid_d.any():
        dmin, dmax = depth[valid_d].min(), depth[valid_d].max()
        with np.errstate(invalid='ignore'):
            norm = (depth - dmin) / (dmax - dmin)
            norm = np.clip(norm, 0.0, 1.0)
        depth_vis = (norm * 255).astype(np.uint8)

    Image.fromarray(img).save(f"{OUT_DIR}/{idx:03d}.png")
    Image.fromarray(depth_vis).save(f"{OUT_DIR}/{idx:03d}_depth.png")
    print(f"Saved fixed view {idx:03d}")

print("Done—check:", OUT_DIR)


/tmp/ipykernel_1034273/2518288703.py:33: RuntimeWarning:

invalid value encountered in cast

/tmp/ipykernel_1034273/2518288703.py:34: RuntimeWarning:

invalid value encountered in cast



Top-5 views: [6, 5, 4, 7, 3]
Saved fixed view 006
Saved fixed view 005
Saved fixed view 004
Saved fixed view 007
Saved fixed view 003
Done—check: scene_init_offscreen_fixed


In [17]:
import json
import numpy as np
import plotly.graph_objects as go
from pathlib import Path

# Load the final 3DGS Gaussians
json_path = Path("scene/gaussians_3dgs_final.json")
assert json_path.exists(), f"Missing: {json_path}"

with open(json_path) as f:
    data = json.load(f)

positions = np.array(data["positions"])
scales = np.array(data["scales"])
shs = np.array(data["shs"])[:, :3]  # only R, G, B from SH

print(f"[INFO] Loaded {len(positions)} Gaussians")
print(f"[INFO] Positions mean: {positions.mean(0)}, min: {positions.min(0)}, max: {positions.max(0)}")
print(f"[INFO] SH color mean: {shs.mean(0)}, max: {shs.max(0)}")

# Filter out invalid/degenerate Gaussians (scale near-zero or NaN)
valid_mask = np.all(np.isfinite(positions), axis=1) & \
             np.all(np.isfinite(scales), axis=1) & \
             (np.linalg.norm(scales, axis=1) > 1e-3)

positions = positions[valid_mask]
shs = shs[valid_mask]
if len(positions) == 0:
    raise RuntimeError("All points filtered out — check input file!")

# Normalize SH colors (clip + scale to 255)
colors = np.clip(shs, 0, 1)
colors_rgb = (colors * 255).astype(np.uint8)

#  Sample only 200 valid points
max_points = 50
if len(positions) > max_points:
    idx = np.random.choice(len(positions), max_points, replace=False)
    positions = positions[idx]
    colors_rgb = colors_rgb[idx]

colors_hex = [f'rgb({r},{g},{b})' for r, g, b in colors_rgb]

# Plot
fig = go.Figure(data=[go.Scatter3d(
    x=positions[:, 0], y=positions[:, 1], z=positions[:, 2],
    mode='markers',
    marker=dict(size=2, color=colors_hex, opacity=0.9)
)])
fig.update_layout(
    scene=dict(
        aspectmode='data',
        xaxis=dict(range=[-1, 1]),
        yaxis=dict(range=[-2.5, 2.5]),
        zaxis=dict(range=[-1, 1]),
    ),
    margin=dict(l=0, r=0, t=40, b=0),
    title="Zoomed View of 200 Sampled Gaussians"
)
fig.show()

print(f"Showing {len(positions)} points")
print("Some positions:", positions[:3])
print("Some colors:", colors_rgb[:3])


[INFO] Loaded 2097152 Gaussians
[INFO] Positions mean: [-1.14920018  4.70065147  2.72777624], min: [-198.60972595 -101.52768707 -180.36012268], max: [205.29234314 115.81006622 201.72792053]
[INFO] SH color mean: [0.33193549 0.27852608 0.27626476], max: [1. 1. 1.]


Showing 50 points
Some positions: [[  2.9305191  -98.99884033  11.85346031]
 [ -3.96938467 109.1530304    9.25987339]
 [-52.82251358 -97.20594025  23.60877419]]
Some colors: [[84 69 72]
 [95 90 97]
 [87 71 71]]


In [18]:
fig.write_html("gaussians_view.html")


In [19]:
import plotly.io as pio
pio.renderers.default = "iframe"
fig.show()
